In [133]:
!pip install mljar-supervised
!pip install tplot

In [134]:
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML

In [135]:
import pandas 
import tplot
import os

In [136]:
SPARCS = pandas.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_sparcs.csv')
SPARCS

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2  Payment Typology 3  \
0      Private Health Insurance                       NaN                 NaN   
1        Blue Cross/Blue Shield                  Self-Pay            Self-Pay   
2                      Self-Pay                  Self-Pay            Self-Pay   
3                      Medicare                  Medicare            Self-Pay   
4        Blue Cross/Blue Shield  

# Experiment 1: Multi-Class Variable


In [137]:
SPARCS['APR Risk of Mortality'].describe()

count     23581
unique        4
top       Minor
freq      13990
Name: APR Risk of Mortality, dtype: object

In [138]:
print(SPARCS['APR Risk of Mortality'].dtypes)

object


In [139]:
SPARCS['APR Risk of Mortality'].value_counts()

Minor       13990
Moderate     4952
Major        3452
Extreme      1187
Name: APR Risk of Mortality, dtype: int64

In [140]:
SPARCS = SPARCS[SPARCS['APR Risk of Mortality'].notna()]

In [141]:
X = SPARCS.drop(columns=['APR Risk of Mortality'])
X

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Severity of Illness Description  \
0      ...                               Minor   
1      ...                               Minor   
2      ...                               Minor   
3      ...                            Moderate   
4      ...                             Extreme   
...    ...                                 ...   
23578  ...                            Moderate   
23579  ...                               Minor   
23580  ...                            Moderate   
23581  ...                               Major   
23582  ...                               Major   

      APR Medical Surgical Description        Payment Typology 1  \
0                              Medical  Private Health Insurance   
1                              Medical    Blue Cross/Blue Shield   
2                              Medical                  Self-Pay   
3                              Medical                  Medicare   
4                              Medical    Blue Cross/Blue Shield   
...                                ...                       ...   
23578                          Medical                  Medicare   
23579                          Medical  Private Health Insurance   
23580                          Medical                

In [142]:
Y = SPARCS['APR Risk of Mortality']
Y

0           Minor
1           Minor
2           Minor
3        Moderate
4           Major
           ...   
23578    Moderate
23579       Minor
23580       Minor
23581       Major
23582       Major
Name: APR Risk of Mortality, Length: 23581, dtype: object

In [143]:
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, stratify=Y, test_size=0.25)

In [144]:
automl = AutoML(
    results_path="SPARCS_APR_Risk_of_Mortality",
    mode="Explain"
)

In [145]:
automl.fit(X_train, Y_train)

Linear algorithm was disabled.
AutoML directory: SPARCS_APR_Risk_of_Mortality
The task is multiclass_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 1.069439 trained in 2.71 seconds
2_DecisionTree logloss 0.591085 trained in 12.63 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost logloss 0.504764 trained in 15.71 seconds
4_Default_NeuralNetwork logloss 0.565377 trained in 4.09 seconds
5_Default_RandomForest logloss 0.547393 trained in 14.0 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.50403 trained in 0.33 seconds
AutoML fit time: 57.08 seconds
AutoML best model: Ensemble


AutoML(results_path='SPARCS_APR_Risk_of_Mortality')

In [146]:
pred = automl.predict(X_test)
pred

array(['Minor', 'Minor', 'Minor', ..., 'Minor', 'Moderate', 'Minor'],
      dtype=object)

In [147]:
automl.report()

In [148]:
AutoML_SPARCS_APR_Risk_of_Mortality = AutoML(results_path="SPARCS_APR_Risk_of_Mortality")

In [149]:
ARM = SPARCS.sample(5)
No_ARM = ARM.drop(columns=['APR Risk of Mortality'])

In [150]:
predict = automl.predict(No_ARM)
predict

array(['Major', 'Moderate', 'Minor', 'Minor', 'Minor'], dtype=object)

In [151]:
values_actual = ARM['APR Risk of Mortality'].values.tolist()
values_predicted = predict.tolist()
output = pandas.DataFrame({'actual': values_actual, 'predicted': values_predicted})
output

actual predicted
0  Moderate     Major
1  Moderate  Moderate
2     Minor     Minor
3     Minor     Minor
4     Minor     Minor

# Experiment 2: Binary Variable

In [152]:
SPARCS['Total Charges'].describe()

count    2.358100e+04
mean     4.342314e+04
std      8.430352e+04
min      1.000000e+00
25%      1.226204e+04
50%      2.375403e+04
75%      4.702532e+04
max      4.410671e+06
Name: Total Charges, dtype: float64

In [153]:
SPARCS['Total Charges'].value_counts()

9973.90     17
8375.20     12
4376.42     11
10575.90     9
4285.44      8
            ..
76670.93     1
28724.91     1
10281.75     1
76073.41     1
32225.00     1
Name: Total Charges, Length: 23180, dtype: int64

In [154]:
X2 = SPARCS.drop(columns=['Total Charges'])
X2

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Severity of Illness Description APR Risk of Mortality  \
0      ...                               Minor                 Minor   
1      ...                               Minor                 Minor   
2      ...                               Minor                 Minor   
3      ...                            Moderate              Moderate   
4      ...                             Extreme                 Major   
...    ...                                 ...                   ...   
23578  ...                            Moderate              Moderate   
23579  ...                               Minor                 Minor   
23580  ...                            Moderate                 Minor   
23581  ...                               Major                 Major   
23582  ...                               Major                 Major   

      APR Medical Surgical Description        Payment Typology 1  \
0                              Medical  Private Health Insurance   
1                              Medical    Blue Cross/Blue Shield   
2                              Medical                  Self-Pay   
3                              Medical                  Medicare   
4                              Medical    Blue Cross/Blue Shie

In [155]:
Y2 = SPARCS['Total Charges']
Y2

0         4757.01
1         5090.25
2         4948.50
3         4719.75
4        50384.75
           ...   
23578    50833.00
23579    10948.00
23580    46421.00
23581    46122.00
23582    32225.00
Name: Total Charges, Length: 23581, dtype: float64

In [156]:
automl2 = AutoML(
      results_path="SPARCS_Total_Charges",
      mode="Explain"
)

In [157]:
automl2.fit(X2, Y2)

Linear algorithm was disabled.
AutoML directory: SPARCS_Total_Charges
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline rmse 92135.993935 trained in 2.3 seconds
2_DecisionTree rmse 49976.021131 trained in 4.63 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost rmse 47653.808562 trained in 26.05 seconds
4_Default_NeuralNetwork rmse 40465.401166 trained in 3.8 seconds
5_Default_RandomForest rmse 63690.166922 trained in 7.74 seconds
* Step ensemble will try to check up to 1 model
Ensemble rmse 32770.852496 trained in 0.19 seconds
AutoML fit time: 51.19 seconds
AutoML best model: Ensemble


AutoML(results_path='SPARCS_Total_Charges')

In [158]:
SPARCS["predictions"] = automl2.predict(X2)


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [159]:
print("Predictions")
print(SPARCS[['Total Charges', 'predictions']].head())

Predictions
   Total Charges   predictions
0        4757.01   6895.885892
1        5090.25   4085.369070
2        4948.50   3885.675883
3        4719.75   8443.861363
4       50384.75  54998.116541


# Downloading Output

In [160]:
os.getcwd()

'c:\\Users\\emman\\Documents\\GitHub\\AutoML-examples'

In [161]:
folders = os.listdir()

In [162]:
print(folders)

['.git', '.gitattributes', 'AutoML.ipynb', 'SPARCS_APR_Risk_of_Mortality', 'SPARCS_Total_Charges']


In [163]:
!zip -r /content/SPARCS_APR_Risk_of_Mortality.zip /content/SPARCS_APR_Risk_of_Mortality

'zip' is not recognized as an internal or external command,
operable program or batch file.


In [164]:
!zip -r /content/SPARCS_Total_Charges.zip /content/SPARCS_Total_Charges


'zip' is not recognized as an internal or external command,
operable program or batch file.
